In [1]:
import pandas as pd
import sqlite3
from shapely.wkt import loads
from shapely.geometry import Point
import geopandas as gpd
import folium
from folium.plugins import FeatureGroupSubGroup
import matplotlib
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt
import osmnx as ox
import googlemaps
import networkx as nx
import gdown

In [2]:
properties = pd.read_csv('/Users/fengcharles/Desktop/CUSP/CUSP 9113D/9113/properties.csv')
mapping = pd.read_csv('/Users/fengcharles/Desktop/CUSP/CUSP 9113D/9113/Primary_Land_Use_Tax_Lot_Output__PLUTO__20241015.csv')

/var/folders/qp/9y56mfxx3zq2c_cjbvf9xg_w0000gn/T/ipykernel_65000/3706016668.py:2: DtypeWarning: Columns (17,18,20,22,24,25,52,61,62,97) have mixed types. Specify dtype option on import or set low_memory=False.
  mapping = pd.read_csv('/Users/fengcharles/Desktop/CUSP/CUSP 9113D/9113/Primary_Land_Use_Tax_Lot_Output__PLUTO__20241015.csv')


In [3]:
conn = sqlite3.connect('DeliveryLockers.db')

cursor = conn.cursor()

In [4]:
mapping.to_sql('mapping', conn, if_exists='replace', index=False)

properties.to_sql('properties', conn, if_exists='replace', index=False)

5689

In [5]:
cursor.execute("""
    SELECT * 
    FROM properties AS p
    LEFT JOIN (select BBL, latitude, longitude from mapping) AS b ON p.bbl = b.BBL;
""")
rows = cursor.fetchall()
columns = [description[0] for description in cursor.description]

conn.close()

mapping_property = pd.DataFrame(rows, columns=columns)

In [6]:
mapping_property = mapping_property.dropna(subset=['latitude', 'longitude'])

columns_to_drop = ['sba_name', 'ccd_name', 'cd_name', 'assessed_value', 'net_inc_sqft', 'gross_exp_sqft', 'inc_tar_info', 'floodplain_flag', 'applied_filters']

mapping_property = mapping_property.drop(columns=columns_to_drop)



In [7]:
downtown_bk_polygon = ox.geocode_to_gdf("Downtown Brooklyn, Brooklyn, New York, USA")

geometry = [Point(xy) for xy in zip(mapping_property['longitude'], mapping_property['latitude'])]
gdf_buildings = gpd.GeoDataFrame(mapping_property, geometry=geometry)

gdf_buildings.set_crs(epsg=4326, inplace=True)

buildings_in_downtown_bk = gdf_buildings[gdf_buildings.within(downtown_bk_polygon.unary_union)]


In [8]:
df= pd.read_csv('/Users/fengcharles/Desktop/CUSP/CUSP 9113D/9113/nyc_delivery_stations_fedex_ups.csv')

In [9]:
place_name_dtbk = "Downtown Brooklyn, Brooklyn, New York, USA"
G_dtbk = ox.graph_from_place(place_name_dtbk, network_type='drive')

nodes_dtbk, edges_dtbk = ox.graph_to_gdfs(G_dtbk)

building_path_data = []

for idx, row in buildings_in_downtown_bk.iterrows():
    lat, lng = row['latitude'], row['longitude']
    
    nearest_node_dtbk = ox.distance.nearest_nodes(G_dtbk, X=lng, Y=lat)
    
    for target_node in nodes_dtbk.index:
        try:
            shortest_distance = nx.shortest_path_length(G_dtbk, nearest_node_dtbk, target_node, weight='length')

            building_path_data.append({
                'building_address': row['standard_address'],
                'building_lat': lat,
                'building_lng': lng,
                'intersection_id': target_node,
                'intersection_lat': G_dtbk.nodes[target_node]['y'],
                'intersection_lng': G_dtbk.nodes[target_node]['x'],
                'shortest_distance_meters': shortest_distance
            })

        except nx.NetworkXNoPath:
            continue

building_path_df = pd.DataFrame(building_path_data)


In [10]:
building_path_df.to_csv('building_path.csv',index=False)

In [11]:
place_name_nyc = "New York City, USA"
G_nyc = ox.graph_from_place(place_name_nyc, network_type='drive')

path_df = []

# Iterate over each row in the df DataFrame (which contains station_name)
for idx, row_df in df.iterrows():
    lat_df, lng_df = row_df['latitude'], row_df['longitude']
    station_name = row_df['name']  # Assuming station_name exists in df
    station_add = row_df['address']
    nearest_node_nyc = ox.distance.nearest_nodes(G_nyc, X=lng_df, Y=lat_df)
    
    # Iterate over each intersection node in Downtown Brooklyn
    for idx_dtbk, node_dtbk in nodes_dtbk.iterrows():
        lat_dtbk, lng_dtbk = node_dtbk['y'], node_dtbk['x']
        nearest_node_dtbk = idx_dtbk  # The node ID in Downtown Brooklyn graph is its index

        try:
            # Calculate the shortest path from the station's nearest node in NYC to the intersection node in Downtown Brooklyn
            shortest_distance = nx.shortest_path_length(G_nyc, nearest_node_nyc, nearest_node_dtbk, weight='length')
            
            # Append the result to DD_data
            path_df.append({
                'station_name': station_name,  # Using the station_name from df
                'station_add': station_add,
                'station_lat': lat_df,
                'station_lng': lng_df,
                'intersection_id': nearest_node_dtbk,
                'intersection_lat': lat_dtbk,
                'intersection_lng': lng_dtbk,
                'shortest_distance': shortest_distance  # Add shortest distance
            })
        except nx.NetworkXNoPath:
            # If no path is found, continue to the next intersection
            continue

# Convert the list of results to a DataFrame
path_df = pd.DataFrame(path_df)


In [12]:
path_df.to_csv('station_path.csv',index=False)

In [13]:
nodes_dtbk, edges_dtbk = ox.graph_to_gdfs(G_dtbk)

# Initialize list to store the path data
DD_data = []

# Iterate over each row in the df DataFrame (which contains station_name)
for idx, row_df in df.iterrows():
    lat_df, lng_df = row_df['latitude'], row_df['longitude']
    station_name = row_df['name']  # Assuming station_name exists in df
    station_add = row_df['address']
    nearest_node_nyc = ox.distance.nearest_nodes(G_nyc, X=lng_df, Y=lat_df)
    
    # Iterate over each building in buildings_in_downtown_bk
    for idx_bk, row_bk in buildings_in_downtown_bk.iterrows():
        lat_bk, lng_bk = row_bk['latitude'], row_bk['longitude']
        nearest_node_bk = ox.distance.nearest_nodes(G_dtbk, X=lng_bk, Y=lat_bk)
        
        try:
            # Calculate the shortest path from nearest_node_nyc to nearest_node_bk
            shortest_distance = nx.shortest_path_length(G_nyc, nearest_node_nyc, nearest_node_bk, weight='length')
            
            # Append the result to DD_data
            DD_data.append({
                'station_name': station_name,  # Using the station_name from df
                'station_add' : station_add,
                'station_lat': lat_df,
                'station_lng': lng_df,
                'building_address': row_bk['standard_address'],
                'building_lat': lat_bk,
                'building_lng': lng_bk,
                'shortest_distance': shortest_distance  # Add shortest distance
            })
        except nx.NetworkXNoPath:
            # If no path is found, continue to the next building
            continue

# Convert the list of results to a DataFrame
DD_data_df = pd.DataFrame(DD_data)

In [14]:
DD_data_df.to_csv('DD_path.csv',index=False)

In [15]:
downtown_bk_location = (40.693943, -73.985880)  # Downtown Brooklyn approximate center
m = folium.Map(location=downtown_bk_location, zoom_start=15)

# Create all required layers (FeatureGroups)
base_group = folium.FeatureGroup(name="Base Map").add_to(m)
stations_layer = folium.FeatureGroup(name="Stations", show=False).add_to(m)
edges_layer = folium.FeatureGroup(name="Edges", show=False).add_to(m)
intersections_layer = folium.FeatureGroup(name="Intersections", show=False).add_to(m)
buildings_layer = folium.FeatureGroup(name="Buildings", show=False).add_to(m)
shortest_path_layer_building = folium.FeatureGroup(name="Shortest Paths to Buildings", show=False).add_to(m)

# Iterate over the DataFrame to calculate shortest paths from `df` to Downtown Brooklyn intersections
for idx, row in df.iterrows():
    lat, lng = row['latitude'], row['longitude']
    nearest_node_nyc = ox.distance.nearest_nodes(G_nyc, X=lng, Y=lat)
    
    for target_node in nodes_dtbk.index:
        try:
            # Calculate the shortest distance and path
            shortest_distance = nx.shortest_path_length(G_nyc, nearest_node_nyc, target_node, weight='length')
            shortest_path = nx.shortest_path(G_nyc, nearest_node_nyc, target_node, weight='length')
            
            # Get coordinates of the shortest path
            path_coords = [(G_nyc.nodes[node]['y'], G_nyc.nodes[node]['x']) for node in shortest_path]
            
            # Add the shortest path to the stations layer (for paths from NYC stations to intersections)
            folium.PolyLine(path_coords, color='blue', weight=2.5, opacity=0.7).add_to(stations_layer)

        except nx.NetworkXNoPath:
            continue

    # Add a marker for each station to the stations layer
    folium.Marker(location=[lat, lng], tooltip=row['name']).add_to(stations_layer)

# Plot the existing Downtown Brooklyn edges
for idx, edge in edges_dtbk.iterrows():
    folium.PolyLine(
        locations=[(coord[1], coord[0]) for coord in edge['geometry'].coords],
        color='green',
        weight=2.5,
        opacity=1
    ).add_to(edges_layer)

# Plot the Downtown Brooklyn intersections
for idx, node in nodes_dtbk.iterrows():
    folium.CircleMarker(
        location=(node['y'], node['x']),
        radius=3,
        color='red',
        fill=True,
        fill_opacity=0.7,
        tooltip=f"Intersection {idx}"
    ).add_to(intersections_layer)

# Plot the buildings in Downtown Brooklyn
for index, row in buildings_in_downtown_bk.iterrows():
    folium.CircleMarker(
        location=[row['latitude'], row['longitude']],
        tooltip=f"{row['standard_address']} | Units:{row['res_units']} | Demand: {row['res_units']*0.44}",
        fill=True,
        color=False,
        fill_color='blue',  
        fill_opacity=0.7
    ).add_to(buildings_layer)

# Plot the actual shortest paths from DD_data to buildings using the road network
for path in DD_data:
    try:
        # Find the nearest nodes for both the source (station) and target (building)
        source_node = ox.distance.nearest_nodes(G_nyc, X=path['station_lng'], Y=path['station_lat'])
        target_node = ox.distance.nearest_nodes(G_dtbk, X=path['building_lng'], Y=path['building_lat'])
        
        # Find the shortest path using the road network
        shortest_path = nx.shortest_path(G_nyc, source_node, target_node, weight='length')
        
        # Get the coordinates for the path
        path_coords = [(G_nyc.nodes[node]['y'], G_nyc.nodes[node]['x']) for node in shortest_path]
        
        # Add the polyline for the shortest path to the shortest_path_layer_building
        folium.PolyLine(
            locations=path_coords,
            color='purple',  # Color for paths to buildings
            weight=2.5,
            opacity=0.8
        ).add_to(shortest_path_layer_building)

        # Add a marker for the building at the end of the path
        folium.Marker(location=[path['building_lat'], path['building_lng']], tooltip=path['building_name']).add_to(shortest_path_layer_building)
    
    except (nx.NetworkXNoPath, KeyError):
        continue

# Plot the actual shortest paths from stations to intersections using the road network
for path in DD_data:
    try:
        # Find the nearest nodes for both the source (station) and target (intersection)
        source_node = ox.distance.nearest_nodes(G_nyc, X=path['station_lng'], Y=path['station_lat'])
        target_node = ox.distance.nearest_nodes(G_dtbk, X=path['intersection_lng'], Y=path['intersection_lat'])
        
        # Find the shortest path using the road network
        shortest_path = nx.shortest_path(G_nyc, source_node, target_node, weight='length')
        
        # Get the coordinates for the path
        path_coords = [(G_nyc.nodes[node]['y'], G_nyc.nodes[node]['x']) for node in shortest_path]
        
        # Add the polyline for the shortest path to the shortest_path_layer_to_intersection
        folium.PolyLine(
            locations=path_coords,
            color='orange',  # Color for paths to intersections
            weight=2.5,
            opacity=0.8
        ).add_to(shortest_path_layer_to_intersection)
    
    except (nx.NetworkXNoPath, KeyError):
        continue

# Add layer control to toggle between layers
folium.LayerControl().add_to(m)

# Display the map
m


In [16]:
file_path = '/Users/fengcharles/Desktop/CUSP/CUSP 9113D/downtown_brooklyn_map.html'
m.save(file_path)